In [1]:
import sys
import os

# Add the root directory to Python path
os.chdir(os.path.abspath('..'))



# Data Preparation

## TMLU

In [10]:
from src.data_loader.tmlu_loader import TMLUDataLoader

# TMLU dataset
tmlu_loader = TMLUDataLoader("miulab/tmlu")
tmlu_dataset = tmlu_loader.load_dataset()

Dataset already exists at ./data/eval\miulab/tmlu. Loading from disk...


In [3]:
tmlu_dataset

DatasetDict({
    test: Dataset({
        features: ['id', 'question', 'A', 'B', 'C', 'D', 'E', 'F', 'answer', 'explanation', 'metadata', 'human_evaluation', 'subject', 'user_content'],
        num_rows: 2796
    })
    dev: Dataset({
        features: ['id', 'question', 'A', 'B', 'C', 'D', 'E', 'F', 'answer', 'explanation', 'metadata', 'human_evaluation', 'subject', 'user_content'],
        num_rows: 185
    })
})

## TaiwanChat

In [2]:
from src.data_loader.taiwanchat_loader import TaiwanChatDataLoader

# TaiwanChat dataset
twchat_loader = TaiwanChatDataLoader("yentinglin/TaiwanChat", cache_dir='./data/fine_tuning')
twchat_dataset = twchat_loader.load_dataset()

c:\Users\l501l\Desktop\TaiwanGPT\.venv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Dataset already exists at ./data/fine_tuning\yentinglin/TaiwanChat. Loading from disk...


In [3]:
twchat_loader = TaiwanChatDataLoader("yentinglin/TaiwanChat", cache_dir='./data/fine_tuning')
twchat_dataset = twchat_loader.load_dataset()
filtered_dataset = twchat_dataset.filter(lambda example: example['dataset_name'] == 'sharegpt')

Dataset already exists at ./data/fine_tuning\yentinglin/TaiwanChat. Loading from disk...


In [4]:
filtered_dataset

Dataset({
    features: ['messages', 'dataset_name', 'instance_id'],
    num_rows: 78767
})

# Token Count

## Eval

In [11]:
from src.data_processor.message_handler import format_dataset_as_messages, num_tokens_from_messages

In [12]:
messages = format_dataset_as_messages(tmlu_dataset)
token_list = [num_tokens_from_messages(message) for message in messages]

In [15]:
messages[0]

[{'role': 'system',
  'content': '\n    你是一個具有廣泛臺灣相關知識的語言模型。你應該能夠提供關於臺灣的各種資訊，\n    包括但不限於臺灣的歷史、文化、地理、政治、經濟、社會習俗以及當前事件。\n    請確保你的回答準確且符合當地的文化背景。\n'},
 {'role': 'user',
  'content': '\n        以下選擇題為出自臺灣的考題，答案為其中一個選項。\n\n        問題:\n        閱讀下文，選出依序最適合填入□內的選項：\n甲、我母親和我姑姑一同出洋去，上船的那天她伏在竹床上痛哭，綠衣綠裙上面釘有□□發光的小片子。(張愛玲〈私語〉)\n乙、蝴蝶的本能是吮吸花蜜，女人的愛亦是一種本能：採集所有美好事物引誘自己進入想像，從自身記憶□□□□並且偷摘他人經驗之片段，想像繁殖成更豐饒的想像，織成一張華麗的密網。（簡媜〈母者〉）\n丙、母親是天可汗，當家的天可汗，一家之王，絕對的威權，分配空間與食物的主人。她要我報告的事，或她突如其來要我□□的事，我最好都要知道，所以我在覲見可汗時，不論她問不問我話，我的心中就是會先有腹稿。(鍾文音〈我的天可汗〉)\n\n        (A) 張揚／綢繆未雨／奏疏 (B) 抽搐／煮繭抽絲／奏疏 (C) 張揚／煮繭抽絲／進貢\t (D) 抽搐／綢繆未雨／進貢\t\n        正確答案：(\n        '}]

In [13]:
sum(token_list)

855922

In [15]:
from openai import OpenAI
from dotenv import load_dotenv
import os
_ = load_dotenv('.env')

client = OpenAI(api_key=os.environ.get("OPENAI_API_KEY", "<your OpenAI API key if not set as env var>"))

example_messages = messages[0]

for model in [
        "gpt-4o-2024-08-06",
        "gpt-4o-mini",
        "gpt-4o-mini-2024-07-18"
    ]:
    print(model)
    # example token count from the function defined above
    print(f"{num_tokens_from_messages(example_messages, model)} prompt tokens counted by num_tokens_from_messages().")
    # example token count from the OpenAI API
    response = client.chat.completions.create(model=model,
    messages=example_messages,
    temperature=0,
    max_tokens=200)
    print(response)
    print(f'{response.usage.prompt_tokens} prompt tokens counted by the OpenAI API.')
    print()

gpt-4o-2024-08-06
478 prompt tokens counted by num_tokens_from_messages().
ChatCompletion(id='chatcmpl-A8DDza4PGaCjfOGRIRXQyn6pMxGYG', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='(B) 抽搐／煮繭抽絲／奏疏', refusal=None, role='assistant', function_call=None, tool_calls=None))], created=1726520823, model='gpt-4o-2024-08-06', object='chat.completion', service_tier=None, system_fingerprint='fp_8080548e81', usage=CompletionUsage(completion_tokens=17, prompt_tokens=478, total_tokens=495, completion_tokens_details={'reasoning_tokens': 0}))
478 prompt tokens counted by the OpenAI API.

gpt-4o-mini
478 prompt tokens counted by num_tokens_from_messages().
ChatCompletion(id='chatcmpl-A8DE0XQbxO1ZfkrKYq7zozpRVpcrK', choices=[Choice(finish_reason='length', index=0, logprobs=None, message=ChatCompletionMessage(content='正確答案是 (C) 張揚／煮繭抽絲／進貢。\n\n解析如下：\n1. 在甲段中，提到「綠衣綠裙上面釘有□□發光的小片子」，這裡的語境需要一個能夠表達出某種引人注目的特質的詞，"張揚"符合這個語境。\n2. 在乙段中，描述女性的愛與本能，提到「從自身記憶□□□□並且偷摘他人

## Fine-tune

In [2]:
from src.data_loader.taiwanchat_loader import TaiwanChatDataLoader
from src.data_processor.message_handler import (
    format_fine_tune_dataset_as_messages,
    check_openai_format_errors,
    num_tokens_from_messages,
    format_fine_tune_dataset_as_openai_input,
    format_fine_tune_dataset_as_openai_input_with_threshold
)

c:\Users\l501l\Desktop\TaiwanGPT\.venv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
twchat_loader = TaiwanChatDataLoader("yentinglin/TaiwanChat", cache_dir='./data/fine_tuning')
twchat_dataset = twchat_loader.load_dataset()
filtered_dataset = twchat_dataset.filter(lambda example: example['dataset_name'] == 'sharegpt')

Dataset already exists at ./data/fine_tuning\yentinglin/TaiwanChat. Loading from disk...


In [4]:
filtered_dataset[:5]

{'messages': [[{'content': '網路搜尋結果：\n\n[1] "6.1. Debrief. 在小組完成任務後，回顧是一個重要的步驟，可以深入了解過程和結果。回顧可以幫助調整教學風格，指出未來需要更多工作或重新檢討的領域，並為所有相關人員提供有價值的反饋。"\n網址：https://peepstrategy.com/group-discussion-steps-to-make-it-better/\n\n[2] "2️⃣ 你可以幫我一下嗎？非常簡單。而且可以用其他情態動詞之一來替換can。你能幫我一下嗎？你會幫我一下嗎？意思完全相同，只是表達方式不同。3️⃣ 我需要一些協助。稍微正式一點。可能是在辦公室的情況。"\n網址：https://www.englishlessonviaskype.com/12-other-ways-to-ask-for-help-in-english/\n\n[3] "請選擇please或kindly。兩者都會使語氣從禮貌轉向需要。please偏向請求，kindly偏向要求。此外，對我來說有點尷尬，因為它在句子中又創造了另一個介系詞片語，因此稀釋了主要內容。我建議省略for me。如果讀者需要幫助理解確認應該是..."\n網址：https://english.stackexchange.com/questions/589801/can-i-ask-a-question-like-could-you-please-kindly-confirm-for-me-in-a-fo/\n\n[4] "以下是比說「根據我上一封郵件」更好的跟進方式。閱讀更多：40個模板幫助您處理最棘手的工作郵件。1. 直接點。有時候最好的方法就是直接指出某人回到原始請求，去除被動攻擊性的措辭。換句話說，行動呼籲是閱讀和..."\n網址：https://www.themuse.com/advice/better-ways-to-follow-up-than-per-my-last-email/\n\n[5] "放鬆。如果您需要幫助的需求與焦慮和恐慌感結合在一起，那麼您會希望做一些事情來幫助自己冷靜下來。建議包括從橫膈膜深呼吸，泡一杯洋甘菊茶，並聽一段放鬆冥想錄音。"\n網址：https://www.verywellmind.com/please-hel

In [8]:
messages = format_fine_tune_dataset_as_messages(filtered_dataset)

In [5]:
openai_input = format_fine_tune_dataset_as_openai_input_with_threshold(filtered_dataset, 2)

In [8]:
openai_input

[{'messages': [{'role': 'system',
    'content': '\n    你是一個具有廣泛臺灣相關知識的語言模型。你應該能夠提供關於臺灣的各種資訊，\n    包括但不限於臺灣的歷史、文化、地理、政治、經濟、社會習俗以及當前事件。\n    請確保你的回答準確且符合當地的文化背景。\n'},
   {'content': '網路搜尋結果：\n\n[1] "6.1. Debrief. 在小組完成任務後，回顧是一個重要的步驟，可以深入了解過程和結果。回顧可以幫助調整教學風格，指出未來需要更多工作或重新檢討的領域，並為所有相關人員提供有價值的反饋。"\n網址：https://peepstrategy.com/group-discussion-steps-to-make-it-better/\n\n[2] "2️⃣ 你可以幫我一下嗎？非常簡單。而且可以用其他情態動詞之一來替換can。你能幫我一下嗎？你會幫我一下嗎？意思完全相同，只是表達方式不同。3️⃣ 我需要一些協助。稍微正式一點。可能是在辦公室的情況。"\n網址：https://www.englishlessonviaskype.com/12-other-ways-to-ask-for-help-in-english/\n\n[3] "請選擇please或kindly。兩者都會使語氣從禮貌轉向需要。please偏向請求，kindly偏向要求。此外，對我來說有點尷尬，因為它在句子中又創造了另一個介系詞片語，因此稀釋了主要內容。我建議省略for me。如果讀者需要幫助理解確認應該是..."\n網址：https://english.stackexchange.com/questions/589801/can-i-ask-a-question-like-could-you-please-kindly-confirm-for-me-in-a-fo/\n\n[4] "以下是比說「根據我上一封郵件」更好的跟進方式。閱讀更多：40個模板幫助您處理最棘手的工作郵件。1. 直接點。有時候最好的方法就是直接指出某人回到原始請求，去除被動攻擊性的措辭。換句話說，行動呼籲是閱讀和..."\n網址：https://www.themuse.com/advice/better-ways-to-follow-up-t

In [6]:
check_openai_format_errors(openai_input)

No errors found


In [9]:
token_list = [num_tokens_from_messages(message['messages']) for message in openai_input]

In [10]:
sum(token_list)

1999693

In [18]:
105794964 / 1_000_000 * 3.00

317.384892